In [1]:
import pandas as pd
from catboost import CatBoostClassifier
from sklearn.metrics import roc_auc_score
import json
from sklearn.model_selection import train_test_split
from collections import Counter
from itertools import combinations
import copy

In [2]:
train = pd.read_csv('../data/train.csv')
label = pd.read_csv('../data/train_label.csv')
test = pd.read_csv('../data/test.csv')
submission = pd.read_csv('../data/submission.csv')
train_data_label = pd.merge(train,label,on='ID')

c2c = ['长期负债合计_年初数','长期负债合计_年末数','其他负债（或长期负债）_年初数','其他负债（或长期负债）_年末数','其他应交款_年初数',
    '其他应交款_年末数','应付福利费_年初数','应付福利费_年末数','预提费用_年初数','预提费用_年末数','待摊费用_年初数','待摊费用_年末数',
    '应收补贴款_年初数','应收补贴款_年末数','长期投资合计_年初数','长期投资合计_年末数','固定资产净额_年初数','固定资产净额_年末数',
    '固定资产净值_年初数','固定资产净值_年末数','无形资产及其他资产合计_年初数','无形资产及其他资产合计_年末数']

/Users/zhaoliang/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [3]:
columns = list(set(train_data_label.columns.to_list()) - set(c2c))
train_data_label = train_data_label[columns]

columns = list(set(test.columns.to_list()) - set(c2c))
test = test[columns]

In [4]:
train_data_label.head()

其他非流动负债_年初数  其他应收款_年初数       投资总额    资产总计_年初数    经营期限至  企业状态  商誉_年末数  \
0          0.0   0.000000  19.110000  844.162546      NaN   0.0     0.0   
1          NaN        NaN  29.154194         NaN      NaN   0.0     NaN   
2          NaN        NaN        NaN         NaN      NaN   0.0     NaN   
3          NaN        NaN        NaN         NaN  42:05.0   0.0     NaN   
4          0.0  22.072334        NaN  397.527613      NaN   0.0     0.0   

   一年内到期的非流动资产_年初数  实收资本（或股本）净额_年初数  商誉_年初数  ...    应收账款_年末数   长期借款_年初数  \
0              0.0              0.0     0.0  ...  142.310005  25.110484   
1              NaN              NaN     NaN  ...         NaN        NaN   
2              NaN              NaN     NaN  ...         NaN        NaN   
3              NaN              NaN     NaN  ...         NaN        NaN   
4              0.0              0.0     0.0  ...  156.901030   0.000000   

     邮政编码  长期借款_年末数  小企业_应付利润_年末数  其他流动负债_年初数  非流动资产合计_年末数  油气资产_年初数  \
0  266300       0.0           0.0         0.0    99.813781       0.0   
1  266000       NaN           NaN         NaN          NaN       NaN   
2  266000       NaN           NaN         NaN          NaN       NaN   
3  266000       NaN           NaN         NaN          NaN       NaN   
4  266400       0.0           0.0         0.0     3.103381       0.0   

   应收票据_年初数  工程物资_年初数  
0  2.647788       0.0  
1       NaN       NaN  
2       NaN       NaN  
3       NaN       NaN  
4  0.000000       0.0  

[5 rows x 157 columns]

In [5]:
def deal_time(x):
    if str(x) == 'nan':
        return x
    
    x = str(x)
    parts = x.split(':')
    return int(parts[0]) + float(parts[1])/100

In [6]:
def cal_diff(x, y):
    if str(x) == 'nan':
        return x
    elif str(y) == 'nan':
        return y
    else:
        return y-x

In [7]:
def deal_manage_range(x):
    g = json.loads(x)
    return len(g)

In [8]:
def deal_cat(x):
    if str(x) == 'nan':
        return -1
    return int(x)

In [9]:
def get_built_tax_rate(x, y, z):  #x:cj y:zz z:xf
    if str(x) == 'nan':
        return x
    elif str(y) == 'nan':
        return y
    elif str(z) == 'nan':
        return z
    elif y+z==0:
        return 0
    else:
        return x/(y+z)

In [10]:
def get_xf_tax(x, y): #消费税 x:jy  y:zz
    if str(x) == 'nan':
        return x
    elif str(y) == 'nan':
        return y
    return x/0.03 - y

In [11]:
def get_tax(x, y): #y->tax
    if str(x) == 'nan':
        return x
    elif str(y) == 'nan':
        return y
    elif y == 0:
        return 0
    return x/y

In [12]:
def divide(x, y):
    if str(x) == 'nan':
        return x
    elif str(y) == 'nan':
        return y
    elif y == 0:
        return 0
    return x/y

In [13]:
def isnll(x):
    if str(x) == 'nan':
        return 0
    return 1

In [14]:
all_ranges = []
jyfw = list(train_data_label['经营范围'])+list(test['经营范围'])
for item in jyfw:
    all_ranges += json.loads(item)
range_dict = dict(Counter(all_ranges))
# bins = [4,8,16,64,128,256,600,3000]
def deal_manage_range_bin(x, lower, upper=100000):
    count = 0
    items = json.loads(x)
    for item in items:
        counts = range_dict.get(item)
        if counts and counts<=upper and counts>lower:
            count += 1
    return count

In [15]:
industry_code_arr = []
industry_code_list = list(train['行业代码'].fillna(-1))+list(test['行业代码'].fillna(-1))
for code in industry_code_list:
    industry_code_arr.append(code)
    
industry_code_map = dict(Counter(industry_code_arr))
def deal_industry_code(x):
    if industry_code_map.get(x) == 4644:
        return 1
    elif industry_code_map.get(x) == 1993:
        return 2
    elif industry_code_map.get(x) == 1272:
        return 0
    elif industry_code_map.get(x) in range(259,1272):
        return 3
    elif industry_code_map.get(x) in range(100,259):
        return 4
    elif industry_code_map.get(x) in range(50,100):
        return 5
    elif industry_code_map.get(x) in range(0,50):
        return 6
    else:
        return 7

In [16]:
def deal_industry_class(x):
    if x>=12:
        return 12
    return x

In [17]:
#企业类型

industry_type_arr = []
industry_type_list = list(train['企业类型'].fillna(-1))+list(test['企业类型'].fillna(-1))
for type_ in industry_type_list:
    industry_type_arr.append(type_)
    
industry_type_map = dict(Counter(industry_type_arr))
def deal_industry_type(x):
    if industry_type_map.get(x)==9311:
        return 1
    elif industry_type_map.get(x)==4406:
        return 2
    elif industry_type_map.get(x)==2750:
        return 3
    elif industry_type_map.get(x)==1262:
        return 4
    elif industry_type_map.get(x) in range(200,1262):
        return 5
    elif industry_type_map.get(x) in range(30, 200):
        return 6
    elif industry_type_map.get(x)<30:
        return 7
    else:
        return 8

In [18]:
def enus2classfify(x):
    if str(x) == 'nan':
        return -1
    else:
        return 0

In [19]:
def gen_feat(raw_table):
    table = copy.copy(raw_table)
    table['经营期限至'] = table['经营期限至'].apply(deal_time)
    table['经营期限自'] = table['经营期限自'].apply(deal_time)
    table['成立日期'] = table['成立日期'].apply(deal_time)
    table['核准日期'] = table['核准日期'].apply(deal_time)
    table['注销时间'] = table['注销时间'].apply(deal_time)

    table['经营期限'] = table.apply(lambda row: cal_diff(row['经营期限自'], row['经营期限至']), axis=1)

    table['消费税'] = table.apply(lambda row: get_xf_tax(row['教育费'], row['增值税']), axis=1)
    table['城建税率'] = table.apply(lambda row: get_built_tax_rate(row['城建税'], row['增值税'], row['消费税']), axis=1)
    table['应纳税额'] = table.apply(lambda row: get_tax(row['企业所得税'], row['城建税率']), axis=1)

    table['经营范围1'] = table['经营范围'].apply(deal_manage_range_bin, args=(0,4,))
    table['经营范围2'] = table['经营范围'].apply(deal_manage_range_bin, args=(4,8,))
    table['经营范围3'] = table['经营范围'].apply(deal_manage_range_bin, args=(8,16,))
    table['经营范围4'] = table['经营范围'].apply(deal_manage_range_bin, args=(16,64,))
    table['经营范围5'] = table['经营范围'].apply(deal_manage_range_bin, args=(64,128,))
    table['经营范围6'] = table['经营范围'].apply(deal_manage_range_bin, args=(128,200,))
    table['经营范围7'] = table['经营范围'].apply(deal_manage_range_bin, args=(200,1000,))
    table['经营范围8'] = table['经营范围'].apply(deal_manage_range_bin, args=(1000,5000,))
    table['经营范围9'] = table['经营范围'].apply(deal_manage_range_bin, args=(5000,))
    
    table['isnull'] = table['在建工程_年末数'].apply(isnll)

    table['经营范围'] = table['经营范围'].apply(deal_manage_range)

    cat_feat = ['行业代码','行业门类','管辖机关', '企业类别','企业类型','登记机关']
    for item in cat_feat:
        table[item] = table[item].apply(deal_cat)

    table['行业代码plus'] = table['行业代码'].apply(deal_industry_code)

    table['行业门类plus'] = table['行业门类'].apply(deal_industry_class)

    table['企业类型plus'] = table['企业类型'].apply(deal_industry_type)

    

    columns = table.columns.tolist()
    columns = list(set(columns)- set(c2c))
    for item in columns:
        parts = item.split("_")
        if len(parts) == 2:
            if parts[1] == '年初数':
                table[parts[0] + '_diff'] = table.apply(lambda row: cal_diff(row[item], row[parts[0]+"_年末数"]), axis=1)

    table['货币资金b/e'] = table.apply(lambda row: divide(row['货币资金_年初数'], row['货币资金_年末数']), axis=1)
    table['货币资金d/e'] = table.apply(lambda row: divide(row['货币资金_年末数'], row['货币资金_diff']), axis=1)
    table['货币资金d/b'] = table.apply(lambda row: divide(row['货币资金_年初数'], row['货币资金_diff']), axis=1)

    table['城建税/增值税'] = table.apply(lambda row: divide(row['城建税'], row['增值税']), axis=1)
    table['城建税/消费税'] = table.apply(lambda row: divide(row['城建税'], row['消费税']), axis=1)


    cat_feats=cat_feat+['行业代码plus','行业门类plus','企业类型plus','isnull']

    feats = table.columns
    return table, feats, cat_feats



In [20]:

drop_feat = ['ID','邮政编码','Label']

In [21]:
train_data, feats, cat_feats = gen_feat(train_data_label)
# feat = [item for item in feats if item not in drop_feat and "年初数" not in item and "年末数" not in item]


feat = [item for item in feats if item not in drop_feat]
# cat_feat = ['管辖机关', '企业类别','行业门类','行业代码','企业状态','邮政编码','登记机关','企业类型']
X = train_data[feat]
y = train_data['Label'].values
x_train,x_test,y_train,y_test = train_test_split(X, y, test_size=0.3,random_state=42)

In [22]:
test_data, _, _ = gen_feat(test)

In [23]:
def make_classifier():
    clf = CatBoostClassifier(
                               loss_function='Logloss',
                               eval_metric="AUC",
                               task_type="CPU",
                               learning_rate=0.01,
                               iterations=20000,
                               od_type="Iter",
        
#                                depth=8,
                               early_stopping_rounds=500,
    #                            l2_leaf_reg=1,
    #                            border_count=96,
                               random_seed=2019
                              )
        
    return clf



In [24]:
cat_feats = list(set(feat)&set(cat_feats))
cat_clf = make_classifier()
cat_clf.fit(x_train, y_train, eval_set=(x_test, y_test),
            use_best_model=True, verbose=500,cat_features=cat_feats)

0:	test: 0.8725157	best: 0.8725157 (0)	total: 95ms	remaining: 31m 39s
500:	test: 0.9231092	best: 0.9231121 (497)	total: 13.9s	remaining: 9m
1000:	test: 0.9249675	best: 0.9251541 (925)	total: 28.1s	remaining: 8m 52s
1500:	test: 0.9269094	best: 0.9269307 (1495)	total: 42.2s	remaining: 8m 40s
2000:	test: 0.9274162	best: 0.9274684 (1841)	total: 1m 18s	remaining: 11m 48s
2500:	test: 0.9279945	best: 0.9280390 (2491)	total: 2m 1s	remaining: 14m 13s
3000:	test: 0.9285583	best: 0.9286308 (2990)	total: 2m 32s	remaining: 14m 24s
3500:	test: 0.9287827	best: 0.9288417 (3450)	total: 2m 46s	remaining: 13m 2s
4000:	test: 0.9288745	best: 0.9291589 (3739)	total: 2m 59s	remaining: 11m 56s
Stopped by overfitting detector  (500 iterations wait)

bestTest = 0.9291588695
bestIteration = 3739

Shrink model to first 3740 iterations.


In [25]:
pd.set_option('max_rows', None)
feature_importance_df = pd.DataFrame()
feature_importance_df["Feature"] = feat
feature_importance_df["importance"] = [item.round(2) for item in cat_clf.feature_importances_]
feature_importance_df.sort_values('importance')

Feature  importance
106   一年内到期的非流动负债_年初数        0.00
38        其他非流动负债_年初数        0.00
45        其他非流动负债_年末数        0.00
52           应付股利_年初数        0.00
62          专项应付款_年末数        0.00
72        递延所得税负债_年初数        0.00
12           开发支出_年末数        0.00
94           应收利息_年末数        0.00
96           递延收益_年末数        0.00
14    一年内到期的非流动负债_年末数        0.00
8         递延所得税资产_年初数        0.00
133       交易性金融资产_年末数        0.00
112       递延所得税资产_年末数        0.00
101          递延收益_年初数        0.00
118       持有至到期投资_年初数        0.01
117          短期投资_年初数        0.01
58       小企业_应付利润_年初数        0.01
138       其他非流动资产_年初数        0.01
71         固定资产清理_年初数        0.01
111      存货中的周转材料_年末数        0.01
85           应付利息_年末数        0.01
86          长期应收款_年末数        0.01
90           短期投资_年末数        0.01
36           预计负债_年末数        0.01
218         递延收益_diff        0.01
110          工程物资_年初数        0.01
105          工程物资_年末数        0.01
76           长期借款_年初数        0.01
29           应收利息_年初数        0.01
139     库存商品(产成品)_年末数        0.01
9           长期应付款_年末数        0.01
203  实收资本（或股本）净额_diff        0.01
26         长期股权投资_年初数        0.01
69          专项应付款_年初数        0.02
28           应付股利_年末数        0.02
220  一年内到期的非流动负债_diff        0.02
100       生产性生物资产_年初数        0.02
75             商誉_年末数        0.02
21           预收款项_年末数        0.02
63          长期应付款_年初数        0.02
22        交易性金融负债_年末数        0.02
51         投资性房地产_年初数        0.02
121          应付票据_年末数        0.02
122      存货中的周转材料_年初数        0.02
91        存货中的原材料_年初数        0.02
130        长期股权投资_年末数        0.02
129     库存商品(产成品)_年初数        0.02
143          长期借款_年末数        0.02
34           预计负债_年初数        0.02
192         盈余公积_diff        0.02
41           盈余公积_年末数        0.02
57        非流动负债合计_年末数        0.03
209     实收资本（股本）_diff        0.03
68    实收资本（或股本）净额_年初数        0.03
229    库存商品(产成品)_diff        0.03
182         资产总计_diff        0.03
123          应付利息_年初数        0.03
55         投资性房地产_年末数        0.03
234      非流动负债合计_diff        0.04
70        其他非流动资产_年末数        0.04
95    一年内到期的非流动资产_年末数        0.04
167            isnull        0.04
88    一年内到期的非流动资产_年初数        0.04
74       可供出售金融资产_年末数        0.04
73       小企业_应付利润_年末数        0.04
152          应收票据_年末数        0.04
31        交易性金融资产_年初数        0.04
60         其他流动资产_年初数        0.04
212       流动资产合计_diff        0.04
187     可供出售金融资产_diff        0.04
54        存货中的原材料_年末数        0.04
15           预收款项_年初数        0.04
23           在建工程_年初数        0.04
189      其他非流动负债_diff        0.04
172         应付票据_diff        0.05
43           在建工程_年末数        0.05
113        流动负债合计_年初数        0.05
171         应收股利_diff        0.05
219   负债和所有者权益总计_diff        0.05
145       非流动负债合计_年初数        0.05
109        其他流动资产_年末数        0.05
18        交易性金融负债_年初数        0.05
175         预收款项_diff        0.05
128         其他应付款_年末数        0.05
64           开发支出_年初数        0.05
65           无形资产_年初数        0.05
33       可供出售金融资产_年初数        0.05
103          短期借款_年末数        0.06
10           短期借款_年初数        0.06
149         长期应收款_年初数        0.06
201         开发支出_diff        0.06
127          应付债券_年初数        0.06
30         长期待摊费用_年初数        0.06
178         资本公积_diff        0.06
16         其他流动负债_年末数        0.06
180         负债合计_diff        0.06
50             存货_年末数        0.06
92         固定资产清理_年末数        0.07
66        生产性生物资产_年末数        0.07
134       持有至到期投资_年末数        0.07
199           存货_diff        0.07
230         应付账款_diff        0.07
188         预计负债_diff        0.07
223         短期投资_diff        0.07
81           油气资产_年初数        0.07
196        其他应收款_diff        0.07
19           资本公积_年初数        0.07
107        应付职工薪酬_年末数        0.08
126          应付账款_年末数        0.08
185      交易性金融资产_diff        0.08
49           油气资产_年末数        0.08
147          应收票据_年初数        0.09
2            无形资产_年末数        0.09
198       其他流动资产_diff        0.09
205       固定资产清理_diff        0.09
142        其他流动负债_年初数        0.09
80          未分配利润_年初数        0.09
20

In [26]:
prob_oof = cat_clf.predict_proba(x_test)
prob_oof = [item[1] for item in prob_oof]
score = roc_auc_score(y_test, prob_oof)
print(score)

prob_oof = cat_clf.predict_proba(x_train)
prob_oof = [item[1] for item in prob_oof]
score = roc_auc_score(y_train, prob_oof)
print(score)

0.9291588694664056
0.9816065166728378


In [24]:
def feat_filter(feature_importance_df, cat_feats, thred = 0.01):
    arr = []
    while((feature_importance_df['importance']<thred).any()):
        filted_feat = list(feature_importance_df[feature_importance_df['importance']>thred]['Feature'])
        X = train_data[filted_feat]
        y = train_data['Label'].values
        x_train,x_test,y_train,y_test = train_test_split(X, y, test_size=0.3,random_state=42)

        cat_clf = make_classifier()
        cat_feats = list(set(cat_feats)&set(filted_feat))
        cat_clf.fit(x_train, y_train, eval_set=(x_test, y_test),
        use_best_model=True, verbose=0,cat_features=cat_feats)

        prob_oof = cat_clf.predict_proba(x_test)
        prob_oof = [item[1] for item in prob_oof]
        test_score = roc_auc_score(y_test, prob_oof)


        prob_oof = cat_clf.predict_proba(x_train)
        prob_oof = [item[1] for item in prob_oof]
        train_score = roc_auc_score(y_train, prob_oof)

        print('round:')
        print('train_auc:',train_score)
        print('test_auc:',test_score)
        print('-----------------------------------')
        pd.set_option('max_rows', None)
        feature_importance_df = pd.DataFrame()
        feature_importance_df["Feature"] = filted_feat
        feature_importance_df["importance"] = [item.round(2) for item in cat_clf.feature_importances_]
        
        arr.append(filted_feat)
    return arr

In [25]:
arr = feat_filter(feature_importance_df, cat_feats, 0.001)

round:
train_auc: 0.9787511162415873
test_auc: 0.9298445395420808
-----------------------------------
round:
train_auc: 0.9816021606081067
test_auc: 0.9298667827180195
-----------------------------------
round:
train_auc: 0.9731477390468308
test_auc: 0.9284678803703972
-----------------------------------
round:
train_auc: 0.9838793712331708
test_auc: 0.9299596238001983
-----------------------------------
round:
train_auc: 0.9746699503097473
test_auc: 0.9289296680447766
-----------------------------------
round:
train_auc: 0.9829510627242206
test_auc: 0.9301844732961001
-----------------------------------
round:
train_auc: 0.9699702231860879
test_auc: 0.9287130388530258
-----------------------------------
round:
train_auc: 0.9761290764209328
test_auc: 0.9302894030608545
-----------------------------------
round:
train_auc: 0.9807270583183723
test_auc: 0.9299721960300766
-----------------------------------
round:
train_auc: 0.9811772887230819
test_auc: 0.9315422741229662
----------------

In [28]:
filted_feats = arr[4]
X = train_data[filted_feats]
y = train_data['Label'].values
x_train,x_test,y_train,y_test = train_test_split(X, y, test_size=0.3,random_state=42)

cat_clf = make_classifier()
cat_feats = list(set(cat_feats)&set(filted_feats))
cat_clf.fit(x_train, y_train, eval_set=(x_test, y_test),
use_best_model=True, verbose=500,cat_features=cat_feats)

prob_oof = cat_clf.predict_proba(x_test)
prob_oof = [item[1] for item in prob_oof]
test_score = roc_auc_score(y_test, prob_oof)


prob_oof = cat_clf.predict_proba(x_train)
prob_oof = [item[1] for item in prob_oof]
train_score = roc_auc_score(y_train, prob_oof)

0:	test: 0.9028742	best: 0.9028742 (0)	total: 22.7ms	remaining: 7m 33s
500:	test: 0.9295341	best: 0.9298987 (484)	total: 4.56s	remaining: 2m 57s
1000:	test: 0.9226726	best: 0.9303068 (536)	total: 8.95s	remaining: 2m 49s
Stopped by overfitting detector  (500 iterations wait)

bestTest = 0.9303068108
bestIteration = 536

Shrink model to first 537 iterations.


In [ ]:
round:
train_auc: 0.9778491774816346
test_auc: 0.9313706148303956
-----------------------------------
round:
train_auc: 0.978490452439552
test_auc: 0.9326674886970817
-----------------------------------
round:
train_auc: 0.984600144372431
test_auc: 0.9330228959647977
-----------------------------------
round:
train_auc: 0.9840691711964553
test_auc: 0.9325673944053577
-----------------------------------
round:
train_auc: 0.9832174827546509
test_auc: 0.93267522545393
-----------------------------------
round:
train_auc: 0.9836698134048558
test_auc: 0.933713885060806
-----------------------------------
round:
train_auc: 0.9773896126525011
test_auc: 0.9308242063779889
-----------------------------------

In [ ]:
filted_feat = list(feature_importance_df[feature_importance_df['importance']>0.01]['Feature'])
X = train_data[filted_feat]
y = train_data['Label'].values
x_train,x_test,y_train,y_test = train_test_split(X, y, test_size=0.3,random_state=42)

In [ ]:
from tpot import TPOTClassifier
tpot = TPOTClassifier(generations= 50, population_size= 20, verbosity= 2, n_jobs=-1, scoring='roc_auc')
tpot.fit(x_train, y_train)
print(tpot.score(x_test, y_test))
tpot.export( 'tpot_boston_pipeline.py')

Imputing missing values in feature set


Generation 1 - Current best internal CV score: 0.921478711563054
Generation 2 - Current best internal CV score: 0.921478711563054
Generation 3 - Current best internal CV score: 0.921478711563054
Generation 4 - Current best internal CV score: 0.921478711563054
Generation 5 - Current best internal CV score: 0.921478711563054
Generation 6 - Current best internal CV score: 0.9231246064758286
Generation 7 - Current best internal CV score: 0.9231246064758286
Generation 8 - Current best internal CV score: 0.9231246064758286
Generation 9 - Current best internal CV score: 0.9231246064758286
Generation 10 - Current best internal CV score: 0.9231246064758286
Generation 11 - Current best internal CV score: 0.9231246064758286
Generation 12 - Current best internal CV score: 0.9231246064758286
Generation 13 - Current best internal CV score: 0.9231246064758286
Generation 14 - Current best internal CV score: 0.9231246064758286
Generation 15 - Current best internal CV score: 0.9231246064758286
Generatio

In [36]:
result = tpot.predict_proba(x_test)

Imputing missing values in feature set


In [37]:
pred_result = [item[1] for item in result]

In [38]:

score = roc_auc_score(y_test, pred_result)
score

0.900550276830831

In [34]:
submission = pd.DataFrame()
submission['ID'] = test_data['ID']
submission['Label'] = pred_result
submission

ID     Label
0         0  0.051254
1         2  0.065557
2         4  0.008691
3         5  0.017020
4         6  0.010179
5         7  0.019520
6         8  0.015058
7        11  0.036850
8        12  0.033882
9        13  0.063485
10       19  0.076449
11       22  0.046672
12       23  0.021871
13       26  0.054913
14       28  0.000213
15       32  0.006650
16       33  0.165967
17       35  0.034766
18       38  0.050781
19       44  0.000000
20       45  0.000000
21       49  0.000000
22       50  0.090921
23       53  0.000000
24       56  0.080862
25       60  0.115043
26       63  0.053693
27       65  0.471628
28       66  0.001738
29       69  0.053544
30       72  0.020785
31       77  0.056374
32       81  0.334075
33       82  0.000000
34       84  0.005980
35       85  0.265983
36       88  0.060210
37       91  0.032086
38       92  0.120616
39       93  0.301572
40       95  0.176902
41       99  0.009746
42      102  0.057979
43      106  0.104026
44      107  0.047474
45      108  0.168792
46      109  0.123871
47      110  0.071963
48      115  0.000629
49      118  0.000000
50      119  0.000455
51      125  0.010798
52      127  0.020652
53      129  0.218863
54      130  0.171530
55      134  0.001875
56      135  0.090004
57      137  0.010814
58      142  0.057048
59      150  0.032473
60      153  0.645163
61      155  0.001667
62      160  0.080853
63      163  0.136678
64      168  0.057046
65      170  0.033290
66      175  0.038284
67      177  0.287412
68      183  0.301294
69      185  0.000000
70      187  0.043309
71      188  0.028317
72      191  0.155669
73      192  0.021241
74      195  0.030255
75      196  0.005419
76      197  0.018894
77      199  0.068766
78      201  0.175993
79      202  0.000769
80      203  0.045124
81      205  0.060900
82      209  0.019324
83      211  0.050268
84      212  0.123994
85      213  0.111877
86      217  0.079090
87      218  0.051416
88      219  0.046618
89      220  0.051856
90      221  0.043471
91      222  0.034563
92      225  0.074154
93      227  0.030197
94      231  0.164336
95      234  0.068987
96      236  0.116310
97      239  0.705873
98      240  0.000500
99      242  0.056219
100     244  0.002338
101     246  0.049131
102     248  0.073925
103     249  0.000000
104     252  0.288099
105     254  0.041443
106     255  0.074180
107     256  0.302535
108     266  0.078632
109     268  0.185709
110     272  0.110759
111     275  0.099129
112     282  0.168572
113     286  0.082064
114     287  0.000833
115     288  0.039733
116     290  0.033645
117     292  0.030663
118     296  0.033399
119     298  0.027018
120     300  0.043874
121     306  0.018106
122     307  0.382676
123     308  0.042780
124     310  0.069688
125     316  0.110032
126     317  0.000000
127     319  0.089357
128     320  0.000102
129     321  0.233525
130     324  0.000000
131     325  0.053560
132     330  0.158090
133     332  0.000000
134     335  0.033516
135     336  0.061848
136     339  0.000259
137     342  0.059850
138     343  0.331203
139     345  0.056143
140     346  0.008481
141     352  0.044861
142     354  0.002513
143     358  0.058303
144     361  0.000629
145     363  0.029156
146     369  0.042039
147     370  0.037483
148     372  0.108950
149     377  0.004000
150     382  0.175939
151     384  0.086791
152     385  0.013107
153     387  0.036275
154     389  0.012080
155     390  0.025418
156     391  0.045144
157     393  0.044242
158     394  0.193596
159     395  0.044552
160     397  0.039826
161     401  0.020246
162     405  0.015178
163     406  0.059691
164     407  0.287412
165     408  0.001667
166     410  0.048957
167     412  0.006856
168     415  0.004848
169     417  0.024282
170     419  0.124138
171     420  0.034507
172     422  0.081230
173     424  0.099624
174     425  0.083982
175     427  0.036189
176     428  0.122154
177     433  0.041553
178     435  0.000000
179     436  0.025039
180     438  0.288101
181  

In [40]:
cat_clf = make_classifier()
cat_clf.fit(x_train, y_train, eval_set=(x_test, y_test),
            use_best_model=True, verbose=500,cat_features=cat_feats)

0:	test: 0.8829226	best: 0.8829226 (0)	total: 33.1ms	remaining: 11m 1s
500:	test: 0.9253766	best: 0.9253766 (500)	total: 14.1s	remaining: 9m 9s
1000:	test: 0.9272160	best: 0.9273330 (998)	total: 28.8s	remaining: 9m 6s
1500:	test: 0.9290037	best: 0.9290037 (1500)	total: 43.4s	remaining: 8m 55s
2000:	test: 0.9307135	best: 0.9307135 (2000)	total: 57.6s	remaining: 8m 38s
2500:	test: 0.9310906	best: 0.9311709 (2333)	total: 1m 11s	remaining: 8m 23s
3000:	test: 0.9316322	best: 0.9316322 (3000)	total: 1m 26s	remaining: 8m 11s
3500:	test: 0.9321409	best: 0.9321428 (3454)	total: 1m 41s	remaining: 7m 58s
4000:	test: 0.9324717	best: 0.9326022 (3890)	total: 1m 56s	remaining: 7m 45s
4500:	test: 0.9325500	best: 0.9327453 (4168)	total: 2m 10s	remaining: 7m 30s
5000:	test: 0.9329784	best: 0.9330229 (4919)	total: 2m 25s	remaining: 7m 17s
Stopped by overfitting detector  (500 iterations wait)

bestTest = 0.933022896
bestIteration = 4919

Shrink model to first 4920 iterations.


In [41]:
prob_oof = cat_clf.predict_proba(x_test)
prob_oof = [item[1] for item in prob_oof]
score = roc_auc_score(y_test, prob_oof)
score

0.9330228959647977

In [42]:
prob_oof = cat_clf.predict_proba(x_train)
prob_oof = [item[1] for item in prob_oof]
score = roc_auc_score(y_train, prob_oof)
score

0.984600144372431

In [29]:
pd.set_option('max_rows', None)
feature_importance_df = pd.DataFrame()
feature_importance_df["Feature"] = filted_feats
feature_importance_df["importance"] = [item.round(2) for item in cat_clf.feature_importances_]
feature_importance_df.sort_values('importance')

Feature  importance
10     在建工程_年初数        0.86
4    其他流动负债_年初数        0.91
9      应收票据_年初数        1.09
8      应收股利_年初数        1.63
14  长期股权投资_diff        1.66
2      负债合计_年初数        2.65
11   流动资产合计_年末数        2.89
15    货币资金_diff        3.15
16  固定资产原价_diff        3.32
6    流动资产合计_年初数        3.40
3    流动负债合计_年初数        3.84
7     其他应收款_年初数        4.71
1           教育费        6.15
5      货币资金_年初数        6.41
0           增值税        6.97
13         应纳税额        8.62
12         城建税率       18.38
17      城建税/消费税       23.35

In [22]:
0.9299755808611977
dropit 0.9304726674886971
ascat 0.9312033074635525

SyntaxError: invalid syntax (<ipython-input-22-5e90baa79963>, line 2)

In [34]:
test['经营期限至'] = test['经营期限至'].apply(deal_time)
test['经营期限自'] = test['经营期限自'].apply(deal_time)
test['成立日期'] = test['成立日期'].apply(deal_time)
test['核准日期'] = test['核准日期'].apply(deal_time)
test['注销时间'] = test['注销时间'].apply(deal_time)

test['经营期限'] = test.apply(lambda row: cal_diff(row['经营期限自'], row['经营期限至']), axis=1)
test['changed'] = test.apply(lambda row: is_changed(row['核准日期'], row['成立日期']), axis=1)

test['消费税'] = test.apply(lambda row: get_xf_tax(row['教育费'], row['增值税']), axis=1)
test['城建税率'] = test.apply(lambda row: get_built_tax_rate(row['城建税'], row['增值税'], row['消费税']), axis=1)
test['应纳税额'] = test.apply(lambda row: get_tax(row['企业所得税'], row['城建税率']), axis=1)

test['经营范围1'] = test['经营范围'].apply(deal_manage_range_bin, args=(0,4,))
test['经营范围2'] = test['经营范围'].apply(deal_manage_range_bin, args=(4,8,))
test['经营范围3'] = test['经营范围'].apply(deal_manage_range_bin, args=(8,16,))
test['经营范围4'] = test['经营范围'].apply(deal_manage_range_bin, args=(16,64,))
test['经营范围5'] = test['经营范围'].apply(deal_manage_range_bin, args=(64,128,))
test['经营范围6'] = test['经营范围'].apply(deal_manage_range_bin, args=(128,256,))
test['经营范围7'] = test['经营范围'].apply(deal_manage_range_bin, args=(256,600,))
test['经营范围8'] = test['经营范围'].apply(deal_manage_range_bin, args=(600,3000,))
test['经营范围9'] = test['经营范围'].apply(deal_manage_range_bin, args=(3000,))

test['经营范围'] = test['经营范围'].apply(deal_manage_range)

cat_feat = ['行业代码','行业门类','管辖机关', '企业类别','企业类型','登记机关']
for item in cat_feat:
    test[item] = test[item].apply(deal_cat)
    
test['行业代码plus'] = test['行业代码'].apply(deal_industry_code)

test['行业门类plus'] = test['行业门类'].apply(deal_industry_class)

test['企业类型plus'] = test['企业类型'].apply(deal_industry_type)

c2c = ['长期负债合计_年初数','长期负债合计_年末数','其他负债（或长期负债）_年初数','其他负债（或长期负债）_年末数','其他应交款_年初数',
'其他应交款_年末数','应付福利费_年初数','应付福利费_年末数','预提费用_年初数','预提费用_年末数','待摊费用_年初数','待摊费用_年末数',
'应收补贴款_年初数','应收补贴款_年末数','长期投资合计_年初数','长期投资合计_年末数','固定资产净额_年初数','固定资产净额_年末数',
'固定资产净值_年初数','固定资产净值_年末数','无形资产及其他资产合计_年初数','无形资产及其他资产合计_年末数']

columns = test.columns.tolist()
columns = list(set(columns)- set(c2c))
for item in columns:
    parts = item.split("_")
    if len(parts) == 2:
        if parts[1] == '年初数':
            test[parts[0] + '_diff'] = test.apply(lambda row: cal_diff(row[item], row[parts[0]+"_年末数"]), axis=1)

for item in c2c:
    test[item] = test[item].apply(enus2classfify)
    



---------------------------------------------------------------------------
TypeError                                 Traceback (most recent call last)
<ipython-input-19-29272e92c9bb> in <module>()
      9 test['应纳税额'] = test.apply(lambda row: get_tax(row['企业所得税'], row['城建税率']), axis=1)
     10 
---> 11 test['经营范围1'] = test['经营范围'].apply(deal_manage_range_bin, args=(0,4,))
     12 test['经营范围2'] = test['经营范围'].apply(deal_manage_range_bin, args=(4,8,))
     13 test['经营范围3'] = test['经营范围'].apply(deal_manage_range_bin, args=(8,16,))

~/anaconda3/lib/python3.6/site-packages/pandas/core/series.py in apply(self, func, convert_dtype, args, **kwds)
   4043             else:
   4044                 values = self.astype(object).values
-> 4045                 mapped = lib.map_infer(values, f, convert=convert_dtype)
   4046 
   4047         if len(mapped) and isinstance(mapped[0], Series):

pandas/_libs/lib.pyx in pandas._libs.lib.map_infer()

~/anaconda3/lib/python3.6/site-packages/pandas/core/series.py in f(x)
   4029 
   4030             def f(x):
-> 4031                 return func(x, *args, **kwds)
   4032 
   4033         else:

<ipython-input-11-31168e103d35> in deal_manage_range_bin(x, lower, upper)
     10     for item in items:
     11         counts = range_dict.get(item)
---> 12         if counts<=upper and counts>lower:
     13             count += 1
     14     return count

TypeError: '<=' not supported between instances of 'NoneType' and 'int'

In [35]:
test_X = test[filted_feats]
result = cat_clf.predict_proba(test_X)

In [36]:
result = [item[1] for item in result]
result

[0.0005293366824749417,
 0.03613565752374427,
 0.002585735991622814,
 0.0015161269188012595,
 0.00158624812760472,
 0.0009524545095219848,
 0.0007120038130775732,
 0.001694371717622933,
 0.0027621101787371665,
 0.0028556945996887372,
 0.0007548480550277118,
 0.0023127425066325276,
 0.003991420233112344,
 0.016831489190690357,
 0.0023484620950662886,
 0.004735428908741838,
 0.22994324113953105,
 0.003781314696630403,
 0.0011284567298747244,
 0.004094058917889714,
 0.0019297035234184935,
 0.0030714382512098868,
 0.003311055833514744,
 0.0016876384400340168,
 0.00217077012692186,
 0.3038554670639643,
 0.0008744449107122831,
 0.45193253370840397,
 0.002235035923269852,
 0.0028833160561546264,
 0.002043208636227297,
 0.0019740037435069476,
 0.35020893159097194,
 0.0007028879566704637,
 0.0032105315962323955,
 0.36311254579081664,
 0.003148020244095431,
 0.0006805564285467836,
 0.0036659071551098893,
 0.4805306516362622,
 0.17967918297772667,
 0.0008073686721325414,
 0.004947681512161565,
 0

In [37]:
submission = pd.DataFrame()
submission['ID'] = test['ID']
submission['Label'] = result
submission

ID     Label
0         0  0.000529
1         2  0.036136
2         4  0.002586
3         5  0.001516
4         6  0.001586
5         7  0.000952
6         8  0.000712
7        11  0.001694
8        12  0.002762
9        13  0.002856
10       19  0.000755
11       22  0.002313
12       23  0.003991
13       26  0.016831
14       28  0.002348
15       32  0.004735
16       33  0.229943
17       35  0.003781
18       38  0.001128
19       44  0.004094
20       45  0.001930
21       49  0.003071
22       50  0.003311
23       53  0.001688
24       56  0.002171
25       60  0.303855
26       63  0.000874
27       65  0.451933
28       66  0.002235
29       69  0.002883
30       72  0.002043
31       77  0.001974
32       81  0.350209
33       82  0.000703
34       84  0.003211
35       85  0.363113
36       88  0.003148
37       91  0.000681
38       92  0.003666
39       93  0.480531
40       95  0.179679
41       99  0.000807
42      102  0.004948
43      106  0.004872
44      107  0.011795
45      108  0.467041
46      109  0.095547
47      110  0.388371
48      115  0.001384
49      118  0.003280
50      119  0.001147
51      125  0.001510
52      127  0.006479
53      129  0.289158
54      130  0.295211
55      134  0.002122
56      135  0.042380
57      137  0.000953
58      142  0.002070
59      150  0.000891
60      153  0.672168
61      155  0.000809
62      160  0.004031
63      163  0.546311
64      168  0.003403
65      170  0.004891
66      175  0.001992
67      177  0.313749
68      183  0.301516
69      185  0.001808
70      187  0.002002
71      188  0.001835
72      191  0.190366
73      192  0.001135
74      195  0.000974
75      196  0.006735
76      197  0.001039
77      199  0.475373
78      201  0.365521
79      202  0.001793
80      203  0.001604
81      205  0.005358
82      209  0.001121
83      211  0.009679
84      212  0.011733
85      213  0.008536
86      217  0.003398
87      218  0.001968
88      219  0.023934
89      220  0.001891
90      221  0.000743
91      222  0.001213
92      225  0.005498
93      227  0.016794
94      231  0.476343
95      234  0.003947
96      236  0.003219
97      239  0.643697
98      240  0.014474
99      242  0.002348
100     244  0.001014
101     246  0.003689
102     248  0.003683
103     249  0.008243
104     252  0.299695
105     254  0.001316
106     255  0.000977
107     256  0.310761
108     266  0.703834
109     268  0.238102
110     272  0.026407
111     275  0.408225
112     282  0.311579
113     286  0.002478
114     287  0.001092
115     288  0.000796
116     290  0.003122
117     292  0.000986
118     296  0.002771
119     298  0.007809
120     300  0.012401
121     306  0.001769
122     307  0.435552
123     308  0.004416
124     310  0.076560
125     316  0.005645
126     317  0.000690
127     319  0.004335
128     320  0.000810
129     321  0.289183
130     324  0.000574
131     325  0.021293
132     330  0.463424
133     332  0.001341
134     335  0.002251
135     336  0.006430
136     339  0.001942
137     342  0.471722
138     343  0.427785
139     345  0.004359
140     346  0.005631
141     352  0.001498
142     354  0.000614
143     358  0.003400
144     361  0.001544
145     363  0.007791
146     369  0.001195
147     370  0.000573
148     372  0.007221
149     377  0.000569
150     382  0.356366
151     384  0.006913
152     385  0.003608
153     387  0.007548
154     389  0.000748
155     390  0.001152
156     391  0.001376
157     393  0.003954
158     394  0.402165
159     395  0.009418
160     397  0.002754
161     401  0.002425
162     405  0.000878
163     406  0.004780
164     407  0.311268
165     408  0.000776
166     410  0.006984
167     412  0.002518
168     415  0.001841
169     417  0.014945
170     419  0.347964
171     420  0.002690
172     422  0.010670
173     424  0.299461
174     425  0.007666
175     427  0.001374
176     428  0.311744
177     433  0.002832
178     435  0.000518
179     436  0.000916
180     438  0.148678
181  

In [38]:
submission.to_csv('submission.csv', index=False, encoding='UTF8')

In [25]:
feat = ['在建工程_年初数','其他流动负债_年初数','应收票据_年初数','应收股利_年初数','长期股权投资_diff',
'负债合计_年初数','流动资产合计_年末数','货币资金_diff','固定资产原价_diff','流动资产合计_年初数',
'流动负债合计_年初数','其他应收款_年初数','教育费','货币资金_年初数','增值税','应纳税额','城建税率','城建税/消费税']

In [27]:
from sklearn.model_selection import KFold
import numpy as np
def cv(X, y, feat, cat, test=None):
    if test is not None:
        test_X = test[feat]
        preds = []

    NFOLDS = 5
    folds = KFold(n_splits=NFOLDS, shuffle=True, random_state=42)
    score = 0
    for fold, (trn_idx, test_idx) in enumerate(folds.split(X, y)):
        clf = make_classifier()
        clf.fit(X.iloc[trn_idx], y[trn_idx], eval_set=(X.iloc[test_idx], y[test_idx]),
                              use_best_model=True, verbose=500)

        result = clf.predict_proba(X.iloc[test_idx])
        result = [item[1] for item in result]
        score += roc_auc_score(y[test_idx], result)

        if test is not None:
            result = clf.predict_proba(test_X)
            result = [item[1] for item in result]
            preds.append(result)
    print(score/NFOLDS)
    if test is not None:
        return preds
    

In [28]:
ar = cv(X,y,feat,cat_feats,test_data)

0:	test: 0.8731975	best: 0.8731975 (0)	total: 29.6ms	remaining: 9m 52s
500:	test: 0.9287493	best: 0.9289949 (453)	total: 8.46s	remaining: 5m 29s
1000:	test: 0.9295697	best: 0.9296565 (982)	total: 17s	remaining: 5m 22s
1500:	test: 0.9309077	best: 0.9310454 (1496)	total: 25.2s	remaining: 5m 10s
2000:	test: 0.9310073	best: 0.9312063 (1725)	total: 33.4s	remaining: 5m
2500:	test: 0.9317525	best: 0.9317567 (2498)	total: 41.7s	remaining: 4m 51s
3000:	test: 0.9323241	best: 0.9323834 (2974)	total: 50.5s	remaining: 4m 45s
3500:	test: 0.9327423	best: 0.9327423 (3500)	total: 1m	remaining: 4m 44s
4000:	test: 0.9335045	best: 0.9335151 (3997)	total: 1m 9s	remaining: 4m 37s
4500:	test: 0.9340062	best: 0.9340486 (4488)	total: 1m 18s	remaining: 4m 29s
Stopped by overfitting detector  (500 iterations wait)

bestTest = 0.9340485894
bestIteration = 4488

Shrink model to first 4489 iterations.
0:	test: 0.8810204	best: 0.8810204 (0)	total: 34.6ms	remaining: 11m 31s
500:	test: 0.9110385	best: 0.9115248 (433)	

In [29]:
pred_result = np.zeros(len(test_data))

In [32]:
pred_result += ar[3]

In [33]:
pred_result/=3

In [34]:
submission = pd.DataFrame()
submission['ID'] = test_data['ID']
submission['Label'] = pred_result
submission

ID     Label
0         0  0.001614
1         2  0.021409
2         4  0.002798
3         5  0.002876
4         6  0.002454
5         7  0.001858
6         8  0.000680
7        11  0.001897
8        12  0.004487
9        13  0.004966
10       19  0.001313
11       22  0.004663
12       23  0.004774
13       26  0.017150
14       28  0.002918
15       32  0.008213
16       33  0.242164
17       35  0.004161
18       38  0.002218
19       44  0.007041
20       45  0.002650
21       49  0.002600
22       50  0.003488
23       53  0.002445
24       56  0.005155
25       60  0.351102
26       63  0.001285
27       65  0.360351
28       66  0.002814
29       69  0.003446
30       72  0.006507
31       77  0.002048
32       81  0.373075
33       82  0.001765
34       84  0.002622
35       85  0.306721
36       88  0.012369
37       91  0.002809
38       92  0.003839
39       93  0.422209
40       95  0.287994
41       99  0.000909
42      102  0.002856
43      106  0.005845
44      107  0.016115
45      108  0.347316
46      109  0.193576
47      110  0.327874
48      115  0.002087
49      118  0.004461
50      119  0.001897
51      125  0.003029
52      127  0.005428
53      129  0.236245
54      130  0.307588
55      134  0.002758
56      135  0.028815
57      137  0.002984
58      142  0.002768
59      150  0.003320
60      153  0.458687
61      155  0.000939
62      160  0.006018
63      163  0.343048
64      168  0.006310
65      170  0.003538
66      175  0.002303
67      177  0.331413
68      183  0.474088
69      185  0.001943
70      187  0.003535
71      188  0.001488
72      191  0.246026
73      192  0.001541
74      195  0.001871
75      196  0.009898
76      197  0.002555
77      199  0.446411
78      201  0.330994
79      202  0.002136
80      203  0.002399
81      205  0.007613
82      209  0.002722
83      211  0.006862
84      212  0.008873
85      213  0.009809
86      217  0.003516
87      218  0.001427
88      219  0.006595
89      220  0.002608
90      221  0.002402
91      222  0.001856
92      225  0.005177
93      227  0.021990
94      231  0.380723
95      234  0.003331
96      236  0.004703
97      239  0.490165
98      240  0.038286
99      242  0.002255
100     244  0.001660
101     246  0.004540
102     248  0.002559
103     249  0.017272
104     252  0.320604
105     254  0.002349
106     255  0.001449
107     256  0.291261
108     266  0.262997
109     268  0.331996
110     272  0.013422
111     275  0.316639
112     282  0.356458
113     286  0.001618
114     287  0.001289
115     288  0.002730
116     290  0.005068
117     292  0.002381
118     296  0.004898
119     298  0.008687
120     300  0.013957
121     306  0.002602
122     307  0.369107
123     308  0.004464
124     310  0.053200
125     316  0.003973
126     317  0.001203
127     319  0.007905
128     320  0.001211
129     321  0.395167
130     324  0.000785
131     325  0.040406
132     330  0.391088
133     332  0.001855
134     335  0.003572
135     336  0.008431
136     339  0.003146
137     342  0.218323
138     343  0.351209
139     345  0.004360
140     346  0.006010
141     352  0.004294
142     354  0.000947
143     358  0.003295
144     361  0.003693
145     363  0.018870
146     369  0.001113
147     370  0.001547
148     372  0.010966
149     377  0.001191
150     382  0.504821
151     384  0.006490
152     385  0.005129
153     387  0.009198
154     389  0.001546
155     390  0.002651
156     391  0.001551
157     393  0.007165
158     394  0.306405
159     395  0.017275
160     397  0.001667
161     401  0.003197
162     405  0.000991
163     406  0.004716
164     407  0.365935
165     408  0.000828
166     410  0.007346
167     412  0.001666
168     415  0.003974
169     417  0.009133
170     419  0.375253
171     420  0.005641
172     422  0.008252
173     424  0.318518
174     425  0.008116
175     427  0.001473
176     428  0.302850
177     433  0.003174
178     435  0.000852
179     436  0.002521
180     438  0.126453
181  

In [35]:
submission.to_csv('submission.csv', index=False, encoding='UTF8')